In [1]:
pip install langchain==0.2.11


[notice] A new release of pip is available: 23.2.1 -> 24.1.2
[notice] To update, run: python.exe -m pip install --upgrade pip


In [2]:
pip install langchain-chroma==0.1.2

Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 23.2.1 -> 24.1.2
[notice] To update, run: python.exe -m pip install --upgrade pip


In [3]:
pip install langchain-core==0.2.24

Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 23.2.1 -> 24.1.2
[notice] To update, run: python.exe -m pip install --upgrade pip


In [4]:
pip install langchain-community==0.2.10

Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 23.2.1 -> 24.1.2
[notice] To update, run: python.exe -m pip install --upgrade pip


In [5]:
pip install langchain-text-splitters==0.2.2

Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 23.2.1 -> 24.1.2
[notice] To update, run: python.exe -m pip install --upgrade pip


In [6]:
pip install pypdf2==3.0.1


Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 23.2.1 -> 24.1.2
[notice] To update, run: python.exe -m pip install --upgrade pip


In [7]:
%pip install -qU langchain-openai==0.1.19

Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 23.2.1 -> 24.1.2
[notice] To update, run: python.exe -m pip install --upgrade pip


In [14]:
import os
import PyPDF2

def extract_text_from_pdf(pdf_path):
    """
    Extract text from a single PDF file.

    :param pdf_path: Path to the PDF file
    :return: Extracted text as a string
    """
    with open(pdf_path, 'rb') as file:
        reader = PyPDF2.PdfReader(file)
        text = ''
        for page_num in range(len(reader.pages)):
            page = reader.pages[page_num]
            text += page.extract_text()
    return text

# Specify the main folder
main_folder = 'data'

# Create a list to store the paths of all PDF files
pdf_files = []
extracted_text = []

# Walk through the directory structure
for root, dirs, files in os.walk(main_folder):
    for file in files:
        if file.endswith('.pdf'):
            # Get the full path to the PDF file and append it to the list
            pdf_files.append(os.path.join(root, file))

# Extract text from each PDF and print it
for pdf_file in pdf_files:
    text = extract_text_from_pdf(pdf_file)
    extracted_text.append(text)


In [15]:
extracted_text

['ACCOUNTANT\nSummary\nFinancial Accountant specializing in financial planning, reporting and analysis within the Department of Defense.\nHighlights\nAccount reconciliations\nResults-oriented\nFinancial reporting\nCritical thinking\nAccounting operations professional\nAnalysis of financial systems\nERP (Enterprise Resource Planning) software.\nExcellent facilitator\nAccomplishments\nServed on a tiger team which identified and resolved General Ledger postings in DEAMS totaling $360B in accounting adjustments. This allowed\nfor the first successful fiscal year-end close for 2012.\nIn collaboration with DFAS Europe, developed an automated tool that identified duplicate obligations. This tool allowed HQ USAFE to\ndeobligate over $5M in duplicate obligations.\nExperience\nCompany Name\n \nJuly 2011\n \nto \nNovember 2012\n \nAccountant\n \nCity\n \n, \nState\nEnterprise Resource Planning Office (ERO)\nIn this position as an Accountant assigned to the Defense Enterprise Accounting and Manage

In [16]:
from langchain_openai import OpenAIEmbeddings
from langchain_text_splitters import CharacterTextSplitter
from langchain.docstore.document import Document
from langchain_chroma import Chroma
import chromadb

# Initialize the text splitter
text_splitter = CharacterTextSplitter(chunk_size=1000, chunk_overlap=0)

# Create embeddings for each extracted text
embeddings = OpenAIEmbeddings()

# Initialize ChromaDB persistent client
persistent_client = chromadb.PersistentClient()
collection_name = "document_embeddings"

# Delete the collection if it exists
try:
    print("collection exists")
    persistent_client.delete_collection(collection_name)
    print("collection deleted")
except KeyError:
    # The collection does not exist
    print("collection doesn't exist")
    pass

# Create a new collection
collection = persistent_client.get_or_create_collection(collection_name)

# Split the documents into chunks and create embeddings
all_embeddings = []
for i, text in enumerate(extracted_text):
    # Wrap text in Document objects
    document = Document(page_content=text)
    chunks = text_splitter.split_documents([document])
    for j, chunk in enumerate(chunks):
        chunk_text = chunk.page_content
        embedding = embeddings.embed_query(chunk_text)
        # Add the embedding to ChromaDB
        collection.add(ids=[f"{i}_{j}"], documents=[chunk_text], embeddings=[embedding])

# Verify the number of items in the collection
langchain_chroma = Chroma(
    client=persistent_client,
    collection_name=collection_name,
    embedding_function=embeddings,
)

print("There are", langchain_chroma._collection.count(), "documents in the collection")

collection exists
collection deleted
There are 2483 documents in the collection


In [17]:
# Example usage of similarity search
query = "sales specialist"
top_docs = langchain_chroma.similarity_search(query)

# Print the top 5 matching documents
print(f"Top {len(top_docs)} documents matching the query:")
for i, doc in enumerate(top_docs):
    print(f"Document {i+1}: {doc.page_content}\n")

Top 4 documents matching the query:
Document 1: SALES SPECIALIST
Objective
To obtain a position in a challenging environment that presents the opportunities for growth and knowledge; where I can maximize and apply my
work ethic, time management skills, management techniques, quality assurance skills, and scientific knowledge.
Education
Bachelor of Science
 
: 
Biology
 
, 
May 2016
 
University of Houston
 
ï¼​ 
City
 
, 
State
 
Minor in Health Science
 
Experience
Sales Specialist
 
December 2014
 
to 
Current
 
Company Name
 
ï¼​ 
City
 
, 
State
Processed sales, payments, credits, refunds and exchanges in a high volume environment.
Assisted customers in person/ remotely with IT setup, including data migration and app installation.
Introduce corporate and small businesses to IT repair, device management, and financing services.
Vice President
 
May 2014
 
to 
Current
 
Company Name
 
ï¼​ 
City
 
, 
State
Negotiated relationships with sponsors, clients, and external organization on m

In [ ]:
# import fitz  # PyMuPDF

# def extract_text_with_pymupdf(pdf_path):
#     # Open the PDF file
#     pdf_document = fitz.open(pdf_path)
    
#     extracted_text = ""
#     for page_num in range(pdf_document.page_count):
#         page = pdf_document.load_page(page_num)
#         extracted_text += page.get_text()
    
#     return extracted_text

# # Example usage
# pdf_path = 'C:\\Users\\rishi\\OneDrive\\Desktop\\Programs\\Pdf_Extractor\\data\\ACCOUNTANT\\10554236.pdf'  # Replace with the actual path to the PDF file
# text = extract_text_with_pymupdf(pdf_path)
# print(text[:2000])  # Displaying the first 2000 characters for analysis
